Iguisa Calabi-Yau
=================

This is the quotient of the product of three 2-tori; For simplicity set $\tau_0=\tau_1=\tau_2=i$ though the complex structures can be abritrary. The quotient is by
$$g(z_0,z_1,z_2)=(z_0+\frac{1}{2},~ -z_1,~ -z_2)$$
and 
$$h(z_0,z_1,z_2)=(-z_0,~ z_1+\frac{1}{2},~ -z_2+\frac{1}{2})$$

In [13]:
from __future__ import print_function
R.<z0, z1, z2> = QQbar[]
F = FreeGroup('g, h, t0r, t0i, t1r, t1i, t2r, t2i')

In [14]:
class IguisaGroupElement(object):
    def __init__(self, group_element, coordinate_mapping, coordinate_inverse, check=False):
        self._g = group_element
        self._map = tuple(coordinate_mapping)
        self._inv = tuple(coordinate_inverse)
        if check: self.check()
        
    def check(self):
        assert (self * self.inverse()).is_identity_map()
        
    def __repr__(self):
        return '{0}: (z0,z1,z2) -> {1}'.format(self._g, self._map)
    
    def __mul__(lhs, rhs):
        g = lhs._g * rhs._g
        img = lhs.image(*rhs.image())
        inv = rhs.preimage(*lhs.preimage())
        return IguisaGroupElement(g, img, inv)
        
    def is_identity_map(self):
        return self._map == self._inv == (z0, z1, z2)
    
    def inverse(self):
        return IguisaGroupElement(self._g^-1, self._inv, self._map)
    
    def image(self, *arg):
        if arg:
            substitution = {z0:arg[0], z1:arg[1], z2:arg[2]}
            return tuple(fwd.subs(substitution) for fwd in self._map)
        else:
            return self._map

    def preimage(self, *arg):
        if arg:
            substitution = {z0:arg[0], z1:arg[1], z2:arg[2]}
            return tuple(inv.subs(substitution) for inv in self._inv)
        else:
            return self._inv

In [15]:
g = IguisaGroupElement(
    F.gens_dict()['g'], 
    [z0+1/2, -z1, -z2], 
    [z0-1/2, -z1, -z2],
    check=True
)

h = IguisaGroupElement(
    F.gens_dict()['h'],
    [-z0, z1+1/2, -z2+1/2],
    [-z0, z1-1/2, -z2+1/2], 
    check=True
)

t0r = IguisaGroupElement(F.gens_dict()['t0r'], [z0+1, z1, z2], [z0-1, z1, z2], check=True)
t0i = IguisaGroupElement(F.gens_dict()['t0i'], [z0+QQbar(I), z1, z2], [z0-QQbar(I), z1, z2], check=True)
t1r = IguisaGroupElement(F.gens_dict()['t1r'], [z0, z1+1, z2], [z0, z1-1, z2], check=True)
t1i = IguisaGroupElement(F.gens_dict()['t1i'], [z0, z1+QQbar(I), z2], [z0, z1-QQbar(I), z2], check=True)
t2r = IguisaGroupElement(F.gens_dict()['t2r'], [z0, z1, z2+1], [z0, z1, z2-1], check=True)
t2i = IguisaGroupElement(F.gens_dict()['t2i'], [z0, z1, z2+QQbar(I)], [z0, z1, z2-QQbar(I)], check=True)

In [16]:
def commutators(*gens):
    """Return all pairwise commutators of the given generators"""
    n = len(gens)
    for i in range(0, len(gens)):
        for j in range(i+1, len(gens)):
            g = gens[i]
            h = gens[j]
            yield g.inverse() * h.inverse() * g * h

In [17]:
relations = [
    g*g * t0r.inverse(), 
    h*h * t1r.inverse(),
    g.inverse() * h.inverse() * g * h * t2r * t1r.inverse() * t0r,
    g * t0r * (t0r * g).inverse(),
    g * t0i * (t0i * g).inverse(),
    g * t1r * (t1r.inverse() * g).inverse(),
    g * t1i * (t1i.inverse() * g).inverse(),
    g * t2r * (t2r.inverse() * g).inverse(),
    g * t2i * (t2i.inverse() * g).inverse(),
    h * t0r * (t0r.inverse() * h).inverse(),
    h * t0i * (t0i.inverse() * h).inverse(),
    h * t1r * (t1r * h).inverse(),
    h * t1i * (t1i * h).inverse(),
    h * t2r * (t2r.inverse() * h).inverse(),
    h * t2i * (t2i.inverse() * h).inverse(),
] + list(commutators(t0r,t0i,t1r,t1i,t2r,t2i))

In [18]:
all(rel.is_identity_map() for rel in relations)

True

In [19]:
G = F.quotient(rel._g for rel in relations)

In [20]:
G.abelian_invariants()

(2, 2, 2, 4, 4)

In [21]:
G.simplified()

Finitely presented group < g, h, t0i, t1i, t2i | g*t0i*g^-1*t0i^-1, t0i^-1*t1i^-1*t0i*t1i, g*t1i*g^-1*t1i, t0i^-1*t2i^-1*t0i*t2i, g*t2i*g^-1*t2i, h*t0i*h^-1*t0i, t1i^-1*t2i^-1*t1i*t2i, h*t1i*h^-1*t1i^-1, h*t2i*h^-1*t2i, g*h^2*g^-1*h^2, h*g^2*h^-1*g^2 >

In [22]:
F.quotient(rel._g for rel in relations + [g*h*g.inverse()*h.inverse()*t0r.inverse()*t1r*t2r]).abelian_invariants()

(2, 2, 2, 4, 4)